In [79]:
import pandas as pd
import numpy as np
from datetime import datetime


import torch
import torch.nn as nn
from torch.utils.data import DataLoader, TensorDataset
from sklearn.preprocessing import StandardScaler

from preprocessing import *
from feature_engineering import *


device = 'cuda' if torch.cuda.is_available() else 'cpu'
device

'cpu'

In [80]:
df = pd.read_csv("E-Building_Data.csv")
df['date_time'] = pd.to_datetime(df['date_time'])
df = df.sort_values(["room_number", "date_time"])

In [81]:
fe = FeatureEngineering(df) # helper class for feature enginerring
df = fe.feature_engineering(n=False)

In [82]:
latitude = 49.0069
longitude = 8.4037
start_date = datetime(2022, 6, 2)
end_date = datetime(2023, 9, 30)
wf = WeatherFetcher(latitude, longitude, start_date, end_date) # helper class to fetch weather
df = wf.combine_weather(df)

c:\Users\Luca-PC\AppData\Local\Programs\Python\Python312\Lib\site-packages\meteostat\interface\meteodata.py:167: FutureWarning:

'H' is deprecated and will be removed in a future version, please use 'h' instead.



In [83]:
df.to_csv("Model_data.csv", index=False)

In [84]:
df = df.drop(['prcp', 'snow', 'wdir', 'wpgt'], axis=1)

In [85]:
df_vanilla = df.drop(['season','temp', 'dwpt', 'rhum',
       'wspd', 'pres', 'tsun', 'coco'], axis=1)
df_seasons = df.drop(['temp', 'dwpt', 'rhum',
       'wspd', 'pres', 'tsun', 'coco'], axis=1)
df_weather = df.drop(['season'], axis=1)
df_combined = df

In [87]:
df_combined = fe.onehotencoding(df_combined, categorical_features=["season", "room_number"])
df_weather = fe.onehotencoding(df_weather, categorical_features=["room_number"])
df_seasons = fe.onehotencoding(df_seasons, categorical_features=["season", "room_number"])
df_vanilla = fe.onehotencoding(df_vanilla, categorical_features=["room_number"])

In [88]:
df_combined_model = df_combined
df_weather_model = df_weather
df_seasons_model = df_seasons.drop(["season"], axis=1)
df_vanilla_model = df_vanilla

In [90]:
def sliding_window_forecast(data: pd.DataFrame, label_name: str, n_in: int, n_out: int, dropna: bool = True) -> pd.DataFrame:
    """
    Transforms time series data into a supervised learning format for forecasting.

    Parameters:
    - data (pd.DataFrame): The input time series data.
    - label_name (str): The name of the target column to forecast.
    - n_in (int): Number of lag observations (input sequence length).
    - n_out (int): Number of future observations to forecast (output sequence length).
    - dropna (bool): Whether to drop rows with NaN values.

    Returns:
    - pd.DataFrame: The transformed DataFrame suitable for forecasting.
    """
    if label_name not in data.columns:
        raise ValueError(f"label_name '{label_name}' is not a column in the data")

    cols, names = list(), list()

    # Input sequence (t-n, ..., t-1, t)
    for i in range(n_in, -1, -1):
        cols.append(data.shift(i))
        names += [f"{col}(t-{i})" if i > 0 else f"{col}(t)" for col in data.columns]

    # Forecast sequence (t+1, ..., t+n)
    for i in range(1, n_out + 1):
        cols.append(data[[label_name]].shift(-i))
        names += [f"{label_name}(t+{i})"]

    
    data_reframed = pd.concat(cols, axis=1)
    data_reframed.columns = names

    if dropna:
        data_reframed.dropna(inplace=True)

    return data_reframed

In [91]:
dataframes = [df_vanilla_model, df_seasons_model, df_weather_model, df_combined_model]
[df.set_index("date_time", inplace=True) for df in dataframes]

[None, None, None, None]

In [93]:
# drop season(t), season(t-1)
df_combined_model.columns

Index(['tmp', 'hum', 'room_number', 'tmp_diff', 'season', 'hour_sin',
       'hour_cos', 'day_of_week_sin', 'day_of_week_cos', 'month_sin',
       'month_cos', 'temp', 'dwpt', 'rhum', 'wspd', 'pres', 'tsun', 'coco',
       'season_autumn', 'season_spring', 'season_summer', 'season_winter',
       'room_number_e001', 'room_number_e002', 'room_number_e003',
       'room_number_e004', 'room_number_e010', 'room_number_e101',
       'room_number_e102', 'room_number_e103', 'room_number_e104',
       'room_number_e106', 'room_number_e109', 'room_number_e113',
       'room_number_e201', 'room_number_e203', 'room_number_e206',
       'room_number_e208', 'room_number_e213', 'room_number_e301',
       'room_number_e302', 'room_number_e303', 'room_number_e304',
       'room_number_e305', 'room_number_e306', 'room_number_e311',
       'room_number_eu02', 'room_number_eu07', 'room_number_eu08',
       'room_number_eu09'],
      dtype='object')

In [94]:
dropped_columns = ["tmp(t+1)", 'season(t-1)', 'room_number(t-1)', 'room_number(t)', 'season(t)']

In [95]:
dataframes = [df_vanilla_model, df_seasons_model, df_weather_model, df_combined_model]
transformed_dataframes = [sliding_window_forecast(df, "tmp", 1, 1) for df in dataframes] # forecarst the next datapoint with the previous datapoint
df_vanilla_model, df_seasons_model, df_weather_model, df_combined_model = transformed_dataframes

In [97]:
df_combined_model.drop(['season(t-1)', 'season(t)'], axis=1, inplace=True)

In [98]:
def prepare_data(df):
    dropped_columns = ["tmp(t+1)", 'room_number(t-1)', 'room_number(t)']
    
    room_dfs_list_train = []
    room_dfs_list_test = []
    
    for room in df["room_number(t)"].unique():
        data = df[df["room_number(t)"] == room].copy()
        room_dfs_list_test.append(data.iloc[int(len(data)*0.8+1):])
        room_dfs_list_train.append(data.iloc[:int(len(data)*0.8+1)])
    
    train_df = pd.concat(room_dfs_list_train)
    test_df = pd.concat(room_dfs_list_test)

    # Drop the specified columns for both training and testing data
    train_input_data = train_df.drop(dropped_columns, axis=1).values
    train_targets = train_df[["tmp(t+1)"]].values
    test_input_data = test_df.drop(dropped_columns, axis=1).values
    test_targets = test_df[["tmp(t+1)"]].values
    
    scaler = StandardScaler()
    train_input_data = scaler.fit_transform(train_input_data)
    test_input_data = scaler.transform(test_input_data)
    
    # Convert to PyTorch tensors
    X_train = torch.tensor(train_input_data, dtype=torch.float32).reshape(-1, 1, train_input_data.shape[1])
    y_train = torch.tensor(train_targets, dtype=torch.float32)
    X_test = torch.tensor(test_input_data, dtype=torch.float32).reshape(-1, 1, test_input_data.shape[1])
    y_test = torch.tensor(test_targets, dtype=torch.float32)

    return X_train, y_train, X_test, y_test

In [99]:
class LSTMNetwork(nn.Module):
    def __init__(self, input_size, hidden_size, output_size, num_layers, ):
        super(LSTMNetwork, self).__init__()
        
        # Bidirectional LSTM layer
        self.bi_lstm = nn.LSTM(input_size, hidden_size, num_layers, bidirectional=True, batch_first=True)
        
        # Dropout layer
        self.dropout = nn.Dropout(p=0.4)
        
        # Fully connected layers
        self.fc1 = nn.Linear(hidden_size*2, hidden_size // 2)

        self.dropout = nn.Dropout(p=0.2)
        
        self.fc2 = nn.Linear(hidden_size // 2, output_size)

    def forward(self, x):
        # Bidirectional LSTM
        x, _ = self.bi_lstm(x)
        
    
        # Take only the last time step output
        x = x[:, -1, :]
        
        # Dropout
        x = self.dropout(x)
        
        # Fully connected layers
        x = self.fc1(x)
        x = torch.relu(x)
        x = self.dropout(x)
        x = self.fc2(x)
        
        return x

### Uncommenct this cell if u want to start train the models, takes about 80min

In [100]:
# def train(model, learning_rate, X_train, y_train, X_test, y_test, batch_size=64, epochs=100):

    
#     criterion = torch.nn.MSELoss()
#     optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
    
#     train_losses = []
#     test_losses = []
    
    
#     train_dataset = TensorDataset(X_train, y_train)
#     train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=False, num_workers=2)
    
    
#     test_dataset = TensorDataset(X_test, y_test)
#     test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False, num_workers=2)
    
#     for epoch in range(epochs):
#         model.train()
        
#         epoch_train_loss = 0.0
#         for batch_X, batch_y in train_loader:
#             optimizer.zero_grad()
            
#             # Forward pass
#             outputs = model(batch_X)
#             loss = criterion(outputs, batch_y)
            
#             # Backward pass and optimization
#             loss.backward()
#             optimizer.step()
            
#             epoch_train_loss += loss.item()
        
#         # Compute average training loss for the epoch
#         train_loss = epoch_train_loss / len(train_loader)
#         train_losses.append(train_loss)
        
#         # Compute test loss
#         model.eval()
#         epoch_test_loss = 0.0
#         with torch.no_grad():
#             for batch_X_test, batch_y_test in test_loader:
#                 test_outputs = model(batch_X_test)
#                 loss = criterion(test_outputs, batch_y_test)
#                 epoch_test_loss += loss.item()
        
#         # Compute average test loss for the epoch
#         test_loss = epoch_test_loss / len(test_loader)
#         test_losses.append(test_loss)
        
#         if (epoch + 1) % 10 == 0 or epoch == 0:
#             print(f'Epoch [{epoch+1}/{epochs}], Train Loss: {train_loss:.4f}, Test Loss: {test_loss:.4f}, Using device: {device}')
    
#     return train_losses, test_losses



# dataframes = [df_vanilla_model, df_seasons_model, df_weather_model, df_combined_model]
# for i, df in enumerate(dataframes, start=0):
#     X_train, y_train, X_test, y_test = prepare_data(df)
#     input_size = X_train.shape[2]
#     hidden_size = 64
#     output_size = 1
#     num_layers = 1
#     epochs = 30
#     batch_size = 32
#     learning_rate = 0.001
#     model = LSTMNetwork(input_size, hidden_size ,output_size ,num_layers)
#     train_losses, test_losses = train(model=model, learning_rate=learning_rate, X_train=X_train, 
#                                     y_train=y_train, X_test=X_test, y_test=y_test, epochs=epochs, batch_size=batch_size)

#     # Save the trained model and losses
#     torch.save(model.state_dict(), f'floor_test_lstm_model.pth')
#     with open(f'floor_test_losses.txt', 'w') as file:
#         file.write("Train Losses:\n")
#         for loss in train_losses:
#             file.write(f"{loss}\n")
#         file.write("\nTest Losses:\n")
#         for loss in test_losses:
#             file.write(f"{loss}\n")

#     print(f'Model for floor {i} trained, saved, and losses recorded.')

In [101]:
dataframes = [df_vanilla_model, df_seasons_model, df_weather_model, df_combined_model]

# Process each dataframe and print the shape
input_data_list = []
for i, df in enumerate(dataframes):
    input_data = df.drop(["tmp(t+1)", "room_number(t)",'room_number(t-1)'], axis=1)
    input_data_list.append(input_data)
    print(f"Shape of input_data{i+1}: {input_data.shape}") # depending of number of rooms in each floor

Shape of input_data1: (185102, 74)
Shape of input_data2: (185102, 82)
Shape of input_data3: (185102, 88)
Shape of input_data4: (185102, 96)


In [102]:
# Directory where the models are stored
model_dir = "trained_models"

# Model details
model_details = [
    {"path": "0_lstm_model.pth", "input_size": 74},
    {"path": "1_lstm_model.pth", "input_size": 82},
    {"path": "2_lstm_model.pth", "input_size": 88},
    {"path": "3_lstm_model.pth", "input_size": 96},
]

models = []
for details in model_details:
    path = os.path.join(model_dir, details["path"])  # Add directory to the path
    input_size = details["input_size"]
    hidden_size = 64
    output_size = 1
    num_layers = 1

    # Instantiate and load the model
    model = LSTMNetwork(input_size, hidden_size ,output_size ,num_layers).to(device)
    model.load_state_dict(torch.load(path))
    model.eval()
    models.append(model)

model_vanilla, model_seasons, model_weather, model_combined = models[:4]

In [103]:
models = [model_vanilla, model_seasons, model_weather, model_combined]
dataframes = [df_vanilla_model, df_seasons_model, df_weather_model, df_combined_model]

results = {
    'True Values': [],
    'Vanilla Predictions': [],
    'Seasons Predictions': [],
    'Weather Predictions': [],
    'Combined Predictions': []
}


device = torch.device("cuda" if torch.cuda.is_available() else "cpu")


for model_name, (df, model) in zip(['Vanilla', 'Seasons', 'Weather', 'Combined'], zip(dataframes, models)):
    X_train, y_train, X_test, y_test = prepare_data(df)

    
    model.to(device)
    X_test = X_test.to(device)
    y_test = y_test.to(device)

    # Set model to evaluation mode
    model.eval()

   
    with torch.no_grad():
        y_pred = model(X_test)

    y_pred = y_pred.cpu().numpy()
    y_test = y_test.cpu().numpy()

    
    results[f'{model_name} True Values'] = y_test.flatten()
    results[f'{model_name} Predictions'] = y_pred.flatten()

# Create individual DataFrames for each floor's predicted and true values
df_results_list = []
for floor in ['Vanilla', 'Seasons', 'Weather', 'Combined']:
    df_result = pd.DataFrame({
        f'{floor} True Values': results[f'{floor} True Values'],
        f'{floor} Predictions': results[f'{floor} Predictions']
    })
    df_results_list.append(df_result)

In [104]:
dataframes = [df_vanilla, df_seasons, df_weather, df_combined]
floor_dfs_list_test = []

for i,df in enumerate(dataframes):
    room_dfs_list = []
    for room in df["room_number"].unique():
        data = df[df["room_number"] == room].copy()
        room_dfs_list.append(data.iloc[int(len(data)*0.8+1):])
    floor_dfs_list_test.append(room_dfs_list)

In [105]:
df_rooms = []
for df in floor_dfs_list_test:
    df_rooms.append(pd.concat(df))

In [106]:
df_plot = []
for df_pred, df_room in zip(df_results_list, df_rooms):
    df_plot.append(df_pred.merge(df_room[["room_number"]].reset_index(), left_index=True, right_index=True, how="right"))

In [107]:
df_plot = pd.concat(df_plot, axis=1)

In [108]:
df_plot = df_plot.drop("index", axis=1)
df_plot = df_plot.loc[:,~df_plot.columns.duplicated()].copy()


In [109]:
def determine_floor(room_number):
    if room_number.startswith('eu'):
        return 'Etage EU'
    elif room_number.startswith('e0'):
        return 'Etage 0'
    elif room_number.startswith('e1'):
        return 'Etage 1'
    elif room_number.startswith('e2'):
        return 'Etage 2'
    elif room_number.startswith('e3'):
        return 'Etage 3'
    
df_plot['Etage'] = df_plot['room_number'].apply(determine_floor)

In [111]:
dropped_columns = ["tmp(t+1)", 'room_number(t-1)', 'room_number(t)']

room_dfs_list_train = []
room_dfs_list_test = []

for room in df_vanilla["room_number"].unique():
    data = df_vanilla[df_vanilla["room_number"] == room].copy()
    room_dfs_list_test.append(data.iloc[int(len(data)*0.8+1):])
    room_dfs_list_train.append(data.iloc[:int(len(data)*0.8+1)])

train_df = pd.concat(room_dfs_list_train)
test_df = pd.concat(room_dfs_list_test)

In [114]:
#df_plot.to_csv("predictions.csv", index=False)

In [115]:
models = [model_vanilla, model_seasons, model_weather, model_combined]
dataframes = [df_vanilla_model, df_seasons_model, df_weather_model, df_combined_model]

results = {
    'True Values': [],
    'Vanilla Predictions': [],
    'Seasons Predictions': [],
    'Weather Predictions': [],
    'Combined Predictions': []
}


for model_name, (df, model) in zip(['Vanilla', 'Seasons', 'Weather', 'Combined'], zip(dataframes, models)):
    X_train, y_train, X_test, y_test = prepare_data(df)

    
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    model.to(device)
    X_test = X_test.to(device)
    y_test = y_test.to(device)

    # Set model to evaluation mode
    model.eval()

    
    with torch.no_grad():
        y_pred = model(X_test)

    y_pred = y_pred.cpu().numpy()
    y_test = y_test.cpu().numpy()

    
    if model_name == 'Vanilla':
        results['True Values'].extend(y_test.flatten())
    results[f'{model_name} Predictions'].extend(y_pred.flatten())

# Debug statement to check lengths of arrays
print("Lengths of arrays in the results dictionary:")
for key, value in results.items():
    print(f"{key}: {len(value)}")

# Ensure all arrays have the same length before creating DataFrame
min_length = min(len(value) for value in results.values())

# Trim all arrays to the same length
for key in results:
    results[key] = results[key][:min_length]


df_results = pd.DataFrame(results)

Lengths of arrays in the results dictionary:
True Values: 37005
Vanilla Predictions: 37005
Seasons Predictions: 37005
Weather Predictions: 37005
Combined Predictions: 37005


In [116]:
import plotly.graph_objects as go

fig = go.Figure()

fig.add_trace(go.Scatter(x=df_plot.index, y=df_plot['Vanilla True Values'], mode='lines', name='True Values'))
fig.add_trace(go.Scatter(x=df_plot.index, y=df_plot['Vanilla Predictions'], mode='lines', name='Vanilla Predictions'))
fig.add_trace(go.Scatter(x=df_plot.index, y=df_plot['Seasons Predictions'], mode='lines', name='Seasons Predictions'))
fig.add_trace(go.Scatter(x=df_plot.index, y=df_plot['Weather Predictions'], mode='lines', name='Weather Predictions'))
fig.add_trace(go.Scatter(x=df_plot.index, y=df_plot['Combined Predictions'], mode='lines', name='Combined Predictions'))


fig.update_layout(title='Vorhersage der Temperatur t+1 mit und ohne Wetter/Jahreszeiten',
                  xaxis_title='Index',
                  yaxis_title='Values')

# Show the plot
fig.show()

In [117]:
from sklearn.metrics import mean_squared_error, mean_absolute_error

# Calculate performance metrics for each model
metrics = {}
for model_name in ['Vanilla Predictions', 'Seasons Predictions', 'Weather Predictions', 'Combined Predictions']:
    true_values = df_results['True Values']
    predictions = df_results[model_name]
    
    mse = mean_squared_error(true_values, predictions)
    mae = mean_absolute_error(true_values, predictions)
    
    metrics[model_name] = {'MSE': mse, 'MAE': mae}

# Print performance metrics
for model_name, metric_vals in metrics.items():
    print(f"Model: {model_name}")
    print(f"MSE: {metric_vals['MSE']:.4f}")
    print(f"MAE: {metric_vals['MAE']:.4f}")

Model: Vanilla Predictions
MSE: 0.3831
MAE: 0.4573
Model: Seasons Predictions
MSE: 0.7995
MAE: 0.6632
Model: Weather Predictions
MSE: 0.5585
MAE: 0.5958
Model: Combined Predictions
MSE: 0.5596
MAE: 0.6204


In [118]:
room = 'e311' # replace it by any other room number
bedingung1 = df_plot['room_number'] == room
bedingung2 = train_df['room_number'] == room

data1 = df_plot[bedingung1].copy()
data2 = train_df[bedingung2].copy()

data1 = data1[["Vanilla Predictions", "date_time", "room_number"]]
data2 = data2[["tmp", "room_number"]]


#test = data2.iloc[:int(len(data2) * 0.8+1)]
df_real = data2.reset_index()
df_pred = data1

new_index_start = len(data2)
df_pred.index = range(new_index_start, new_index_start + len(data1))

df_real = pd.concat([df_real, df_pred.copy().rename(columns={"Vanilla Predictions": "tmp"})])

fig = go.Figure()


fig.add_trace(go.Scatter(x=df_real.index, y=df_real['tmp'],
                         mode='lines', name='Real', line=dict(color='red')))


fig.add_trace(go.Scatter(x=df_pred.index, y=df_pred['Vanilla Predictions'],
                         mode='lines', name='Predicted', line=dict(color='blue')))


cutoff_index = len(data2)
fig.add_shape(
    dict(
        type="line",
        x0=cutoff_index,
        y0=min(df_real['tmp'].min()-1, df_pred['Vanilla Predictions'].min()-1),
        x1=cutoff_index,
        y1=max(df_real['tmp'].max()+1, df_pred['Vanilla Predictions'].max()+1),
        line=dict(
            color="black",
            width=3,
            dash="dash",
        ),
    )
)


fig.update_layout(
    title='Temperature True Value and Prediction',
    xaxis_title='Index',
    yaxis_title='Temperature',
    showlegend=True,
    width=1500,
    height=500
)


fig.show()

In [128]:
from sklearn.preprocessing import StandardScaler


X_train, y_train, X_test, y_test = prepare_data(df_vanilla_model.iloc[:100])  


scaler = StandardScaler()
scaler.fit(y_train)

model = model_vanilla
# Sequential prediction
model.eval()
sequential_predictions = []

# Use the first window to start the prediction
current_window = X_test[0]  # Shape [1, 74]

with torch.no_grad():
    for i in range(len(X_test)):
       
        x = current_window.unsqueeze(0)
        print(f"Step {i} - Input shape to model: {x.shape}")
        print(f"Step {i} - current_window: {current_window}")
        
        # Make prediction
        prediction = model(x).item()
        print(f"Step {i} - Prediction: {prediction}")
        sequential_predictions.append(prediction)
        
        # Prepare the next window
        if i < len(X_test) - 1:
            # Normalize the prediction
            prediction_array = np.array(prediction).reshape(-1, 1)  # Reshape to 2D array
            normalized_prediction = scaler.transform(prediction_array)[0, 0]
            next_value = torch.tensor([normalized_prediction], dtype=torch.float32).view(1, 1)  
            current_window = torch.cat((current_window[:, 1:], next_value), dim=1)  # Shape: [1, 74]
            print(f"Step {i} - Updated current_window shape: {current_window.shape}")
            print(f"Step {i} - Updated current_window: {current_window}")


sequential_predictions = np.array(sequential_predictions)

print(f'Sequential Predictions shape: {sequential_predictions.shape}')

Step 0 - Input shape to model: torch.Size([1, 1, 74])
Step 0 - current_window: tensor([[-0.2384,  0.6006, -0.3409, -0.2402,  1.3897, -0.4484,  1.4180,  0.0000,
          0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,
          0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,
          0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,
          0.0000,  0.0000,  0.0000,  0.0000,  0.0000, -0.3994,  0.5170, -0.4520,
          0.1185,  1.4036,  1.4226,  1.9763,  0.0000,  0.0000,  0.0000,  0.0000,
          0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,
          0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,
          0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,
          0.0000,  0.0000]])
Step 0 - Prediction: 21.16743278503418
Step 0 - Updated current_window shape: torch.Size([1, 74])
Step 0 - Updated current_window: tensor([[ 0.6006, -0.3409, -0.24

In [130]:
# Flatten y_train and y_test for plotting
y_train = y_train.flatten()
y_test = y_test.flatten()


train_indices = np.arange(len(y_train))
test_indices = np.arange(len(y_train), len(y_train) + len(sequential_predictions))


fig = go.Figure()


fig.add_trace(go.Scatter(x=train_indices, y=y_train, mode='lines', name='Real - Train', line=dict(color='red')))


fig.add_trace(go.Scatter(x=test_indices, y=y_test, mode='lines', name='Real - Test', line=dict(color='green')))


fig.add_trace(go.Scatter(x=test_indices, y=sequential_predictions, mode='lines', name='Predicted - Test', line=dict(color='blue')))


fig.add_shape(type="line", x0=len(y_train), y0=min(min(y_train), min(y_test)), x1=len(y_train), y1=max(max(y_train), max(y_test)),
              line=dict(color="black", dash="dash"))

fig.update_layout(
    title="Temperature True Values and Predictions",
    xaxis_title="Time Index",
    yaxis_title="Temperature",
    legend_title="Legend",
    font=dict(size=14)
)


fig.show()